In [1]:
import warnings
warnings.filterwarnings(action='ignore')
%config Completer.use_jedi = False
import numpy as np
import pandas as pd
import requests
import json
import folium
from pandas.io.json import json_normalize

In [2]:
# 따릉이 서버에 post 방식으로 요청해서 서버가 응답하는 데이터를 받는다.
targetSite = 'https://www.bikeseoul.com/app/station/getStationRealtimeStatus.do'
request = requests.post(targetSite, data={
    'stationGrpSeq': 'ALL'
})
# print(request) # <Response [200]>
# print(type(request.text)) # <class 'str'>
# print(request.text)

In [3]:
# 따릉이 서버가 응답하는 json 형태의 문자열을 파이썬에서 사용하기 위해서 딕셔너리 타입으로 변환한다.
# bike_json = json.loads(request.text) # json 모듈의 loads() 메소드 사용
bike_json = request.json() # requests 모듈의 json() 메소드 사용
# print(type(bike_json)) # <class 'dict'>
# print(bike_json.keys())
# print(bike_json)

In [4]:
# bike_json['realtimeList']
bike_json.get('realtimeList')

[{'stationName': '102. 망원역 1번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-4',
  'stationLongitude': '126.91062927',
  'stationLatitude': '37.55564880',
  'rackTotCnt': '15',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '13',
  'parkingELECBikeCnt': '3',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '103. 망원역 2번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-5',
  'stationLongitude': '126.91083527',
  'stationLatitude': '37.55495071',
  'rackTotCnt': '14',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '3',
  'parkingELECBikeCnt': '4',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '104. 합정역 1번출구 앞',
  'stationImgFileName': '',
  'stationId': 'ST-6',
  'stationLongitude': '126.91508484',
  'stationLatitude': '37.55073929',
  'rackTotCnt': '13',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '3',
  'parkingELECBikeCnt': '2',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationName': '105. 합정역 5번출구 앞',
  'stationImgFileName': '',

In [5]:
# pandas.io.json 모듈의 json_normalize() 메소드로 json 타입의 데이터가 변환된 딕셔너리를 데이터프레임으로 변환한다.
# json_normalize(딕셔너리, 데이터프레임으로 변환할 데이터가 할당된 딕셔너리의 key)
bike_df = json_normalize(bike_json, 'realtimeList')
bike_df

stationName stationImgFileName stationId stationLongitude  \
0       102. 망원역 1번출구 앞                         ST-4     126.91062927   
1       103. 망원역 2번출구 앞                         ST-5     126.91083527   
2       104. 합정역 1번출구 앞                         ST-6     126.91508484   
3       105. 합정역 5번출구 앞                         ST-7     126.91482544   
4       106. 합정역 7번출구 앞                         ST-8     126.91282654   
...                 ...                ...       ...              ...   
2723  6058. 서울도시건축전시관 옆                      ST-3297     126.97684479   
2724  6058. 서울도시건축전시관 옆                      ST-3297     126.97684479   
2725       6171. 월드빌딩 앞                      ST-3276     126.83743286   
2726     6172. 가양5단지아파트                      ST-3281     126.85464478   
2727  6173. 서울자동차운전전문학원                      ST-3284     126.82106018   

     stationLatitude rackTotCnt parkingBikeTotCnt parkingQRBikeCnt  \
0        37.55564880         15                 0               13   
1        37.55495071         14                 0                3   
2        37.55073929         13                 0                3   
3        37.55000687          5                 0                0   
4        37.54864502         12                 0                1   
...              ...        ...               ...              ...   
2723     37.56653976         10                 0                1   
2724     37.56653976         10                 0                1   
2725     37.54098129         12                 0               24   
2726     37.56447983         10                 0                0   
2727     37.54613495         10                 0               19   

     parkingELECBikeCnt stationSeCd  mode  
0                     3     RAK_002  None  
1                     4     RAK_002  None  
2                     2     RAK_002  None  
3                     1     RAK_002  None  
4                     0     RAK_002  None  
...                 ...         ...   ...  
2723                  0     RAK_002  None  
2724                  0     RAK_002  None  
2725                  0     RAK_002  None  
2726                  0     RAK_002  None  
2727                  0     RAK_002  None  

[2728 rows x 11 columns]

In [6]:
bike_df.columns

Index(['stationName', 'stationImgFileName', 'stationId', 'stationLongitude',
       'stationLatitude', 'rackTotCnt', 'parkingBikeTotCnt',
       'parkingQRBikeCnt', 'parkingELECBikeCnt', 'stationSeCd', 'mode'],
      dtype='object')

In [7]:
# stationId: 대여소 id
# stationName: 대여소 이름
# parkingBikeTotCnt: 주차된 따릉이 LCD형 대수 => 사용하지 않음
# parkingQRBikeCnt: 주차된 따릉이 QR형 대수 => 일반 따릉이
# parkingELECBikeCnt: 주차된 새싹 따릉이 대수
# stationLongitude: 대여소 경도
# stationLatitude: 대여소 위도
# rackTotCnt: 주차 가능한 자전거 대수

In [8]:
bike_df_map = bike_df[['stationId', 'stationName', 'parkingQRBikeCnt', 'parkingELECBikeCnt', 
                       'stationLongitude', 'stationLatitude']]
del bike_df
bike_df_map

stationId        stationName parkingQRBikeCnt parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞               13                  3   
1         ST-5    103. 망원역 2번출구 앞                3                  4   
2         ST-6    104. 합정역 1번출구 앞                3                  2   
3         ST-7    105. 합정역 5번출구 앞                0                  1   
4         ST-8    106. 합정역 7번출구 앞                1                  0   
...        ...                ...              ...                ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                1                  0   
2724   ST-3297  6058. 서울도시건축전시관 옆                1                  0   
2725   ST-3276       6171. 월드빌딩 앞               24                  0   
2726   ST-3281     6172. 가양5단지아파트                0                  0   
2727   ST-3284  6173. 서울자동차운전전문학원               19                  0   

     stationLongitude stationLatitude  
0        126.91062927     37.55564880  
1        126.91083527     37.55495071  
2        126.91508484     37.55073929  
3        126.91482544     37.55000687  
4        126.91282654     37.54864502  
...               ...             ...  
2723     126.97684479     37.56653976  
2724     126.97684479     37.56653976  
2725     126.83743286     37.54098129  
2726     126.85464478     37.56447983  
2727     126.82106018     37.54613495  

[2728 rows x 6 columns]

In [9]:
# bike_df_map.dtypes
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2728 entries, 0 to 2727
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stationId           2728 non-null   object
 1   stationName         2728 non-null   object
 2   parkingQRBikeCnt    2728 non-null   object
 3   parkingELECBikeCnt  2728 non-null   object
 4   stationLongitude    2728 non-null   object
 5   stationLatitude     2728 non-null   object
dtypes: object(6)
memory usage: 128.0+ KB


In [10]:
bike_df_map['parkingQRBikeCnt'] = bike_df_map.parkingQRBikeCnt.astype(int)
bike_df_map['parkingELECBikeCnt'] = bike_df_map.parkingELECBikeCnt.astype(int)
bike_df_map['stationLongitude'] = bike_df_map.stationLongitude.astype(float)
bike_df_map['stationLatitude'] = bike_df_map.stationLatitude.astype(float)
bike_df_map['parkingTotBikeCnt'] = bike_df_map.parkingQRBikeCnt + bike_df_map.parkingELECBikeCnt
bike_df_map

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                13                   3   
1         ST-5    103. 망원역 2번출구 앞                 3                   4   
2         ST-6    104. 합정역 1번출구 앞                 3                   2   
3         ST-7    105. 합정역 5번출구 앞                 0                   1   
4         ST-8    106. 합정역 7번출구 앞                 1                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2725   ST-3276       6171. 월드빌딩 앞                24                   0   
2726   ST-3281     6172. 가양5단지아파트                 0                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLongitude  stationLatitude  parkingTotBikeCnt  
0           126.910629        37.555649                 16  
1           126.910835        37.554951                  7  
2           126.915085        37.550739                  5  
3           126.914825        37.550007                  1  
4           126.912827        37.548645                  1  
...                ...              ...                ...  
2723        126.976845        37.566540                  1  
2724        126.976845        37.566540                  1  
2725        126.837433        37.540981                 24  
2726        126.854645        37.564480                  0  
2727        126.821060        37.546135                 19  

[2728 rows x 7 columns]

In [11]:
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2728 entries, 0 to 2727
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   stationId           2728 non-null   object 
 1   stationName         2728 non-null   object 
 2   parkingQRBikeCnt    2728 non-null   int32  
 3   parkingELECBikeCnt  2728 non-null   int32  
 4   stationLongitude    2728 non-null   float64
 5   stationLatitude     2728 non-null   float64
 6   parkingTotBikeCnt   2728 non-null   int32  
dtypes: float64(2), int32(3), object(2)
memory usage: 117.3+ KB


In [12]:
bike_df_map.to_csv('./data/bike_df_map.csv', index=False)

Geo Coding

지오코딩 => 주소로 위도, 경도 얻기, 역지오코딩 => 위도, 경도로 주소 얻기  
pip install geopy

GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /search?q=%EC%84%9C%EC%9A%B8%EC%8B%9C+%EC%A2%85%EB%A1%9C%EA%B5%AC+%EA%B4%80%EC%B2%A0%EB%8F%99&format=json&limit=1 (Caused by SSLError(SSLCertVerificationError(1, '[SSL: CERTIFICATE_VERIFY_FAILED] certificate verify failed: certificate has expired (_ssl.c:1091)')))  
위와 같은 에러가 발생되면 아래의 코드를 추가하고 실행한다.  

import certifi  
import ssl  
import geopy.geocoders  

ctx = ssl.create_default_context(cafile=certifi.where())  
geopy.geocoders.options.default_ssl_context = ctx

In [13]:
from geopy.geocoders import Nominatim

In [14]:
# 지오코딩 함수 => 주소를 인수로 넘겨받아 위도, 경도를 리턴하는 함수
def geocoding(address):
    geocoder = Nominatim(user_agent='South Korea', timeout=None)
    geo = geocoder.geocode(address)
    return {'위도': geo.latitude, '경도': geo.longitude}

In [15]:
'''
address = geocoding('서울시 종로구 관철동')
print(address)
address = geocoding('경기도 양주시 양주2동')
print(address)
'''
pass

In [16]:
# 역지오코딩 함수 => 위도, 경도를 넘겨받아 주소를 리턴하는 함수
def geocoding_reverse(lat_lot):
    geocoder = Nominatim(user_agent='South Korea', timeout=None)
    return geocoder.reverse(lat_lot)

In [17]:
'''
address = geocoding_reverse('37.79867678, 127.08181639')
# print(type(address)) # <class 'geopy.location.Location'>
# print(address)
addr = str(address).split(', ')
# print(type(addr)) # <class 'list'>
# ['부흥로', '고읍동', '양주시', '11493', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('37.5711455, 126.9883295')
addr = str(address).split(', ')
# ['탑골공원', '99', '종로', '청진동', '종로3가', '종로1·2·3·4가동', '종로구', '서울특별시', '03140', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('35.15869706, 129.1603842')
addr = str(address).split(', ')
# ['해운대 해수욕장', '해운대해변로', '우1동', '해운대구', '부산광역시', '48093', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('36.7711151, 128.074248')
addr = str(address).split(', ')
# ['문경세제오픈세트장', '문경새재 오픈세트장', '문경시', '경상북도', '36919', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('37.555649, 126.910629')
addr = str(address).split(', ')
# ['스타벅스', '74', '월드컵로', '서교동', '마포구', '서울특별시', '04004', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('37.546135, 126.821060')
addr = str(address).split(', ')
# ['222', '남부순환로', '외발산동', '발산1동', '강서구', '서울특별시', '07506', '대한민국']
print(addr[-3], addr[-4], addr[-5])
'''
pass

In [18]:
bike_df_map['goo'] = np.NaN
bike_df_map['dong'] = np.NaN
bike_df_map

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                13                   3   
1         ST-5    103. 망원역 2번출구 앞                 3                   4   
2         ST-6    104. 합정역 1번출구 앞                 3                   2   
3         ST-7    105. 합정역 5번출구 앞                 0                   1   
4         ST-8    106. 합정역 7번출구 앞                 1                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 1                   0   
2725   ST-3276       6171. 월드빌딩 앞                24                   0   
2726   ST-3281     6172. 가양5단지아파트                 0                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                19                   0   

      stationLongitude  stationLatitude  parkingTotBikeCnt  goo  dong  
0           126.910629        37.555649                 16  NaN   NaN  
1           126.910835        37.554951                  7  NaN   NaN  
2           126.915085        37.550739                  5  NaN   NaN  
3           126.914825        37.550007                  1  NaN   NaN  
4           126.912827        37.548645                  1  NaN   NaN  
...                ...              ...                ...  ...   ...  
2723        126.976845        37.566540                  1  NaN   NaN  
2724        126.976845        37.566540                  1  NaN   NaN  
2725        126.837433        37.540981                 24  NaN   NaN  
2726        126.854645        37.564480                  0  NaN   NaN  
2727        126.821060        37.546135                 19  NaN   NaN  

[2728 rows x 9 columns]

In [19]:
'''
for i in range(bike_df_map.shape[0])[:]:
    lat_lot = '{},{}'.format(bike_df_map.loc[i, 'stationLatitude'], bike_df_map.loc[i, 'stationLongitude'])
    # print(lat_lot)
    address = geocoding_reverse(lat_lot)
    addr = str(address).split(', ')
    # print(i, addr[-4], addr[-5])
    try:
        bike_df_map.loc[i, 'goo'] = addr[-4]
    except:
        print('{}번째 인덱스 스테이션의 -4번째 주소 없음'.format(i))
    try:
        bike_df_map.loc[i, 'dong'] = addr[-5]
    except:
        print('{}번째 인덱스 스테이션의 -5번째 주소 없음'.format(i))
    if (i + 1) % 20 == 0:
        print('============', i + 1, '============')
        
bike_df_map
'''
pass

In [20]:
# bike_df_map.to_csv('./data/bike_20240508.csv', index=False)
# bike_df_map = pd.read_csv('./data/bike_20240508.csv', encoding='cp949')
bike_df_map = pd.read_csv('./data/bike_20240508.csv')
bike_df_map

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                 2                   5   
1         ST-5    103. 망원역 2번출구 앞                 0                   5   
2         ST-6    104. 합정역 1번출구 앞                27                   2   
3         ST-7    105. 합정역 5번출구 앞                 1                   1   
4         ST-8    106. 합정역 7번출구 앞                 0                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 0                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 0                   0   
2725   ST-3276       6171. 월드빌딩 앞                10                   0   
2726   ST-3281     6172. 가양5단지아파트                 1                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                18                   0   

      stationLongitude  stationLatitude  parkingTotBikeCnt  goo  dong  
0           126.910629        37.555649                  7  마포구   서교동  
1           126.910835        37.554951                  5  마포구  망원1동  
2           126.915085        37.550739                 29  마포구   서교동  
3           126.914825        37.550007                  2  마포구   서교동  
4           126.912827        37.548645                  0  마포구   합정동  
...                ...              ...                ...  ...   ...  
2723        126.976845        37.566540                  0   중구   소공동  
2724        126.976845        37.566540                  0   중구   소공동  
2725        126.837433        37.540981                 10  강서구  화곡1동  
2726        126.854645        37.564480                  1  강서구  가양2동  
2727        126.821060        37.546135                 18  강서구  발산1동  

[2728 rows x 9 columns]

In [21]:
bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()]

stationId          stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
44      ST-212      155. 가좌역1 번출구 앞                 1                   4   
64      ST-232      179. 가좌역 4번출구 앞                 0                  15   
1356   ST-2352      2079.중앙대학교 중앙광장                 3                   3   
2097   ST-3225  3934. 철도교통관제센터 정문 앞                11                   0   
2532   ST-3024   4837. 양원지구 힐데스하임 앞                14                   2   

      stationLongitude  stationLatitude  parkingTotBikeCnt    goo dong  
44          126.915047        37.568295                  5   성산2동  NaN  
64          126.915298        37.568775                 15  남가좌1동  NaN  
1356        126.957779        37.506672                  6    흑석동  NaN  
2097        126.877884        37.497082                 11   구로1동  NaN  
2532        127.106209        37.609241                 16   망우본동  NaN

In [22]:
bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()].stationId

44       ST-212
64       ST-232
1356    ST-2352
2097    ST-3225
2532    ST-3024
Name: stationId, dtype: object

In [23]:
errorList = list(bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()].stationId)
print(type(errorList))
print(errorList)

<class 'list'>
['ST-212', 'ST-232', 'ST-2352', 'ST-3225', 'ST-3024']


In [24]:
for error in errorList:
    bike_error = bike_df_map[bike_df_map.stationId == error]
    # print(bike_error)
    lat_lot = '{},{}'.format(bike_error.iloc[0, 5], bike_error.iloc[0, 4])
    # lat_lot = '{},{}'.format(bike_error.loc[bike_error.index[0], 'stationLatitude'], bike_error.loc[bike_error.index[0], 'stationLongitude'])
    # print(lat_lot)
    address = geocoding_reverse(lat_lot)
    addr = str(address).split(', ')
    # print(addr)
    bike_df_map.loc[bike_error.index, 'goo'] = addr[-3]
    bike_df_map.loc[bike_error.index, 'dong'] = addr[-4]
    
bike_df_map[bike_df_map.goo.isnull() | bike_df_map.dong.isnull()]

Empty DataFrame
Columns: [stationId, stationName, parkingQRBikeCnt, parkingELECBikeCnt, stationLongitude, stationLatitude, parkingTotBikeCnt, goo, dong]
Index: []

In [26]:
bike_df_map.to_csv('./data/bike_20240508_ok.csv', index=False)
bike_df_map_ok = pd.read_csv('./data/bike_20240508_ok.csv')
bike_df_map_ok

stationId        stationName  parkingQRBikeCnt  parkingELECBikeCnt  \
0         ST-4    102. 망원역 1번출구 앞                 2                   5   
1         ST-5    103. 망원역 2번출구 앞                 0                   5   
2         ST-6    104. 합정역 1번출구 앞                27                   2   
3         ST-7    105. 합정역 5번출구 앞                 1                   1   
4         ST-8    106. 합정역 7번출구 앞                 0                   0   
...        ...                ...               ...                 ...   
2723   ST-3297  6058. 서울도시건축전시관 옆                 0                   0   
2724   ST-3297  6058. 서울도시건축전시관 옆                 0                   0   
2725   ST-3276       6171. 월드빌딩 앞                10                   0   
2726   ST-3281     6172. 가양5단지아파트                 1                   0   
2727   ST-3284  6173. 서울자동차운전전문학원                18                   0   

      stationLongitude  stationLatitude  parkingTotBikeCnt  goo  dong  
0           126.910629        37.555649                  7  마포구   서교동  
1           126.910835        37.554951                  5  마포구  망원1동  
2           126.915085        37.550739                 29  마포구   서교동  
3           126.914825        37.550007                  2  마포구   서교동  
4           126.912827        37.548645                  0  마포구   합정동  
...                ...              ...                ...  ...   ...  
2723        126.976845        37.566540                  0   중구   소공동  
2724        126.976845        37.566540                  0   중구   소공동  
2725        126.837433        37.540981                 10  강서구  화곡1동  
2726        126.854645        37.564480                  1  강서구  가양2동  
2727        126.821060        37.546135                 18  강서구  발산1동  

[2728 rows x 9 columns]

서울시 따릉이 스테이션 위치 시각화

In [36]:
bike = bike_df_map_ok
bike_map_seoul = folium.Map(location=[bike.stationLatitude.mean(), bike.stationLongitude.mean()], zoom_start=12)

for index, data in bike.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0]
    else:
        stationName = station[1]
    '''
    stationName = station[0] if len(station) == 1 else station[1]
    string = '{} => 일반: {}대, 새싹: {}대'.format(stationName.strip(), data.parkingQRBikeCnt, data.parkingELECBikeCnt)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo,
                 icon=folium.Icon(color='green', icon='ok')).add_to(bike_map_seoul)

bike_map_seoul.save('./output/bike_map_seoul.html')
bike_map_seoul

종로구 따릉이 스테이션 위치 시각화

In [38]:
bike = bike_df_map_ok[bike_df_map_ok.goo.str.find('종로') >= 0]
bike_map_seoul = folium.Map(location=[bike.stationLatitude.mean(), bike.stationLongitude.mean()], zoom_start=14)

for index, data in bike.iterrows():
    
    station = data.stationName.split('.')
    stationName = station[0] if len(station) == 1 else station[1]
    string = '{} => 일반: {}대, 새싹: {}대'.format(stationName.strip(), data.parkingQRBikeCnt, data.parkingELECBikeCnt)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker(location=[data.stationLatitude, data.stationLongitude], popup=stationInfo,
                 icon=folium.Icon(color='green', icon='ok')).add_to(bike_map_seoul)

bike_map_seoul.save('./output/bike_map_seoul.html')
bike_map_seoul